# (Optional) Colab Setup
If you aren't using Colab, you can delete the following code cell. This is just to help students with mounting to Google Drive to access the other .py files and downloading the data, which is a little trickier on Colab than on your local machine using Jupyter. 

In [1]:
# # you will be prompted with a window asking to grant permissions
# from google.colab import drive
# drive.mount("/content/drive")

In [2]:
# # fill in the path in your Google Drive in the string below. Note: do not escape slashes or spaces
# import os
# datadir = "/content/assignment1"
# if not os.path.exists(datadir):
#   !ln -s "/content/drive/My Drive/YOUR PATH HERE/assignment1/" $datadir
# os.chdir(datadir)
# !pwd

In [3]:
# # downloading Fashion-MNIST
# import os
# os.chdir(os.path.join(datadir,"fashion-mnist/"))
# !chmod +x ./get_data.sh
# !./get_data.sh
# os.chdir(datadir)

# Imports

In [1]:
import random
import numpy as np
from data_process import get_FASHION_data, get_RICE_data
from scipy.spatial import distance
from models import Perceptron, SVM, Softmax, Logistic
from kaggle_submission import output_submission_csv
%matplotlib inline

# For auto-reloading external modules
# See http://stackoverflow.com/questions/1907993/autoreload-of-modules-in-ipython
%load_ext autoreload
%autoreload 2

# Loading Fashion-MNIST

In the following cells we determine the number of images for each split and load the images.
<br /> 
TRAIN_IMAGES + VAL_IMAGES = (0, 60000]
, TEST_IMAGES = 10000

In [2]:
# You can change these numbers for experimentation
# For submission we will use the default values 
TRAIN_IMAGES = 50000
VAL_IMAGES = 10000
normalize = True

In [3]:
data = get_FASHION_data(TRAIN_IMAGES, VAL_IMAGES, normalize=normalize)
X_train_fashion, y_train_fashion = data['X_train'], data['y_train']
X_val_fashion, y_val_fashion = data['X_val'], data['y_val']
X_test_fashion, y_test_fashion = data['X_test'], data['y_test']
n_class_fashion = len(np.unique(y_test_fashion))

# Loading Rice

In [4]:
# loads train / test / val splits of 80%, 20%, 20% 
data = get_RICE_data()
X_train_RICE, y_train_RICE = data['X_train'], data['y_train']
X_val_RICE, y_val_RICE = data['X_val'], data['y_val']
X_test_RICE, y_test_RICE = data['X_test'], data['y_test']
n_class_RICE = len(np.unique(y_test_RICE))

print("Number of train samples: ", X_train_RICE.shape[0])
print("Number of val samples: ", X_val_RICE.shape[0])
print("Number of test samples: ", X_test_RICE.shape[0])

Number of train samples:  10911
Number of val samples:  3637
Number of test samples:  3637


### Get Accuracy

This function computes how well your model performs using accuracy as a metric.

In [5]:
def get_acc(pred, y_test):
    return np.sum(y_test == pred) / len(y_test) * 100

In [12]:
print('X_train_RICE', X_train_RICE)
print('Y_train_RICE', y_train_RICE)
print('X_train_fashion', X_train_fashion)
print('y_train_fashion', y_train_fashion)

X_train_RICE [[6.48500000e+03 5.65300000e+03 1.49098010e+02 ... 3.30327000e+02
  6.51029553e-01 3.01491124e+00]
 [1.56090000e+04 7.47100000e+03 1.47544293e+02 ... 3.48779000e+02
  7.71770091e-01 2.25414994e+00]
 [1.39540000e+04 8.48200000e+03 1.55140680e+02 ... 3.73781000e+02
  7.62910670e-01 2.19843235e+00]
 ...
 [1.27250000e+04 9.06000000e+03 1.58431151e+02 ... 3.92347000e+02
  7.39600829e-01 2.15688949e+00]
 [7.93600000e+03 7.02200000e+03 1.67978647e+02 ... 3.74547000e+02
  6.29010715e-01 3.10674259e+00]
 [1.46640000e+04 9.06900000e+03 1.61453745e+02 ... 3.86285000e+02
  7.63754140e-01 2.22164340e+00]]
Y_train_RICE [1 0 0 ... 0 1 0]
X_train_fashion [[-9.00000e-04 -6.16000e-03 -3.09400e-02 ... -2.67578e+00 -8.04120e-01
  -7.32000e-02]
 [-9.00000e-04 -6.16000e-03 -3.09400e-02 ... -2.67578e+00 -8.04120e-01
  -7.32000e-02]
 [-9.00000e-04 -6.16000e-03 -3.09400e-02 ... -2.67578e+00 -8.04120e-01
  -7.32000e-02]
 ...
 [-9.00000e-04 -6.16000e-03 -3.09400e-02 ... -2.67578e+00 -8.04120e-01
  -

# Perceptron

Perceptron has 2 hyperparameters that you can experiment with:
- **Learning rate** - controls how much we change the current weights of the classifier during each update. We set it at a default value of 0.5, but you should experiment with different values. We recommend changing the learning rate by factors of 10 and observing how the performance of the classifier changes. You should also try adding a **decay** which slowly reduces the learning rate over each epoch.
- **Number of Epochs** - An epoch is a complete iterative pass over all of the data in the dataset. During an epoch we predict a label using the classifier and then update the weights of the classifier according to the perceptron update rule for each sample in the training set. You should try different values for the number of training epochs and report your results.

You will implement the Perceptron classifier in the **models/perceptron.py**

The following code: 
- Creates an instance of the Perceptron classifier class 
- The train function of the Perceptron class is trained on the training data
- We use the predict function to find the training accuracy as well as the testing accuracy


## Train Perceptron on Fashion-MNIST

In [9]:
import sys
np.set_printoptions(threshold=sys.maxsize)

lr = 0.1
n_epochs = 100

percept_fashion = Perceptron(n_class_fashion, lr, n_epochs)
percept_fashion.train(X_train_fashion, y_train_fashion)

In [10]:
pred_percept = percept_fashion.predict(X_train_fashion)
print('The training accuracy is given by: %f' % (get_acc(pred_percept, y_train_fashion)))

The training accuracy is given by: 9.940000


### Validate Perceptron on Fashion-MNIST

In [11]:
pred_percept = percept_fashion.predict(X_val_fashion)
print('The validation accuracy is given by: %f' % (get_acc(pred_percept, y_val_fashion)))

The validation accuracy is given by: 9.790000


### Test Perceptron on Fashion-MNIST

In [12]:
pred_percept = percept_fashion.predict(X_test_fashion)
print('The testing accuracy is given by: %f' % (get_acc(pred_percept, y_test_fashion)))

The testing accuracy is given by: 9.910000


### Perceptron_Fashion-MNIST Kaggle Submission

Once you are satisfied with your solution and test accuracy, output a file to submit your test set predictions to the Kaggle for Assignment 1 Fashion-MNIST. Use the following code to do so:

In [13]:
output_submission_csv('kaggle/perceptron_submission_fashion.csv', percept_fashion.predict(X_test_fashion))

## Train Perceptron on Rice

In [14]:
lr = 0.5
n_epochs = 10

percept_RICE = Perceptron(n_class_RICE, lr, n_epochs)
percept_RICE.train(X_train_RICE, y_train_RICE)

In [15]:
pred_percept = percept_RICE.predict(X_train_RICE)
print('The training accuracy is given by: %f' % (get_acc(pred_percept, y_train_RICE)))

The training accuracy is given by: 54.779580


### Validate Perceptron on Rice

In [16]:
pred_percept = percept_RICE.predict(X_val_RICE)
print('The validation accuracy is given by: %f' % (get_acc(pred_percept, y_val_RICE)))

The validation accuracy is given by: 56.145175


### Test Perceptron on Rice

In [17]:
pred_percept = percept_RICE.predict(X_test_RICE)
print('The testing accuracy is given by: %f' % (get_acc(pred_percept, y_test_RICE)))

The testing accuracy is given by: 54.055540


# Support Vector Machines (with SGD)

Next, you will implement a "soft margin" SVM. In this formulation you will maximize the margin between positive and negative training examples and penalize margin violations using a hinge loss.

We will optimize the SVM loss using SGD. This means you must compute the loss function with respect to model weights. You will use this gradient to update the model weights.

SVM optimized with SGD has 3 hyperparameters that you can experiment with:
- **Learning rate** - similar to as defined above in Perceptron, this parameter scales by how much the weights are changed according to the calculated gradient update. 
- **Epochs** - similar to as defined above in Perceptron.
- **Regularization constant** - Hyperparameter to determine the strength of regularization. In this case it is a coefficient on the term which maximizes the margin. You could try different values. The default value is set to 0.05.

You will implement the SVM using SGD in the **models/svm.py**

The following code: 
- Creates an instance of the SVM classifier class 
- The train function of the SVM class is trained on the training data
- We use the predict function to find the training accuracy as well as the testing accuracy

## Train SVM on Fashion-MNIST

In [18]:
lr = 0.5
n_epochs = 10
reg_const = 0.05

svm_fashion = SVM(n_class_fashion, lr, n_epochs, reg_const)
svm_fashion.train(X_train_fashion, y_train_fashion)

[[-9.00000e-04 -6.16000e-03 -3.09400e-02 ... -2.67578e+00 -8.04120e-01
  -7.32000e-02]
 [-9.00000e-04 -6.16000e-03 -3.09400e-02 ... -2.67578e+00 -8.04120e-01
  -7.32000e-02]
 [-9.00000e-04 -6.16000e-03 -3.09400e-02 ... -2.67578e+00 -8.04120e-01
  -7.32000e-02]
 ...
 [-9.00000e-04 -6.16000e-03 -3.09400e-02 ... -2.67578e+00 -8.04120e-01
  -7.32000e-02]
 [-9.00000e-04 -6.16000e-03 -3.09400e-02 ... -2.67578e+00 -8.04120e-01
  -7.32000e-02]
 [-9.00000e-04 -6.16000e-03 -3.09400e-02 ... -2.67578e+00 -8.04120e-01
  -7.32000e-02]]


c:\Users\azaan\OneDrive\Desktop\Deep Learning for Computer Vision HW\assignment1_cs444\models\svm.py:42: RuntimeWarning: overflow encountered in scalar negative
  


In [20]:
pred_svm = svm_fashion.predict(X_train_fashion)
print('The training accuracy is given by: %f' % (get_acc(pred_svm, y_train_fashion)))

weights [ 5.90152022e-25 -5.22173439e-25  2.82103032e-25  2.39361989e-24
  2.68355234e-23  8.88616122e-23  1.69776097e-22  2.41501196e-22
  2.52282463e-22 -1.53507341e-23 -6.56442018e-22 -7.84248323e-22
 -2.69435564e-23  2.27749746e-22  2.60363012e-22  4.92224072e-22
 -5.20067640e-22 -1.08609645e-21 -4.86645262e-22  3.55478642e-24
  1.54230488e-22  8.91688212e-23  1.43199135e-22  3.79013570e-23
  4.93230573e-24  1.88592102e-24 -1.34982150e-23 -1.97138288e-24
 -1.05701862e-24 -4.77654373e-24 -1.17510418e-23  3.56747689e-24
  9.34785994e-23  2.32395940e-22  4.32549502e-22  2.29771074e-22
 -1.99241852e-23 -6.30730047e-22 -1.03438919e-21 -6.77743522e-22
 -4.72566318e-22 -5.97882156e-22 -8.34554527e-22 -7.90058641e-22
 -6.37273112e-22 -1.03507698e-21 -7.54234918e-22 -6.46398646e-22
 -4.16723331e-22  1.06697878e-22  1.96110489e-22  9.60698785e-23
 -4.57088226e-24  4.38404609e-24 -9.62787158e-24 -1.56332333e-23
 -3.93929983e-24 -1.13293377e-23 -9.38096446e-24  2.09027796e-23
  2.18624041e-22 

### Validate SVM on Fashion-MNIST

In [21]:
pred_svm = svm_fashion.predict(X_val_fashion)
print('The validation accuracy is given by: %f' % (get_acc(pred_svm, y_val_fashion)))

weights [ 5.90152022e-25 -5.22173439e-25  2.82103032e-25  2.39361989e-24
  2.68355234e-23  8.88616122e-23  1.69776097e-22  2.41501196e-22
  2.52282463e-22 -1.53507341e-23 -6.56442018e-22 -7.84248323e-22
 -2.69435564e-23  2.27749746e-22  2.60363012e-22  4.92224072e-22
 -5.20067640e-22 -1.08609645e-21 -4.86645262e-22  3.55478642e-24
  1.54230488e-22  8.91688212e-23  1.43199135e-22  3.79013570e-23
  4.93230573e-24  1.88592102e-24 -1.34982150e-23 -1.97138288e-24
 -1.05701862e-24 -4.77654373e-24 -1.17510418e-23  3.56747689e-24
  9.34785994e-23  2.32395940e-22  4.32549502e-22  2.29771074e-22
 -1.99241852e-23 -6.30730047e-22 -1.03438919e-21 -6.77743522e-22
 -4.72566318e-22 -5.97882156e-22 -8.34554527e-22 -7.90058641e-22
 -6.37273112e-22 -1.03507698e-21 -7.54234918e-22 -6.46398646e-22
 -4.16723331e-22  1.06697878e-22  1.96110489e-22  9.60698785e-23
 -4.57088226e-24  4.38404609e-24 -9.62787158e-24 -1.56332333e-23
 -3.93929983e-24 -1.13293377e-23 -9.38096446e-24  2.09027796e-23
  2.18624041e-22 

### Test SVM on Fashion-MNIST

In [22]:
pred_svm = svm_fashion.predict(X_test_fashion)
print('The testing accuracy is given by: %f' % (get_acc(pred_svm, y_test_fashion)))

weights [ 5.90152022e-25 -5.22173439e-25  2.82103032e-25  2.39361989e-24
  2.68355234e-23  8.88616122e-23  1.69776097e-22  2.41501196e-22
  2.52282463e-22 -1.53507341e-23 -6.56442018e-22 -7.84248323e-22
 -2.69435564e-23  2.27749746e-22  2.60363012e-22  4.92224072e-22
 -5.20067640e-22 -1.08609645e-21 -4.86645262e-22  3.55478642e-24
  1.54230488e-22  8.91688212e-23  1.43199135e-22  3.79013570e-23
  4.93230573e-24  1.88592102e-24 -1.34982150e-23 -1.97138288e-24
 -1.05701862e-24 -4.77654373e-24 -1.17510418e-23  3.56747689e-24
  9.34785994e-23  2.32395940e-22  4.32549502e-22  2.29771074e-22
 -1.99241852e-23 -6.30730047e-22 -1.03438919e-21 -6.77743522e-22
 -4.72566318e-22 -5.97882156e-22 -8.34554527e-22 -7.90058641e-22
 -6.37273112e-22 -1.03507698e-21 -7.54234918e-22 -6.46398646e-22
 -4.16723331e-22  1.06697878e-22  1.96110489e-22  9.60698785e-23
 -4.57088226e-24  4.38404609e-24 -9.62787158e-24 -1.56332333e-23
 -3.93929983e-24 -1.13293377e-23 -9.38096446e-24  2.09027796e-23
  2.18624041e-22 

### SVM_Fashion-MNIST Kaggle Submission

Once you are satisfied with your solution and test accuracy output a file to submit your test set predictions to the Kaggle for Assignment 1 Fashion-MNIST. Use the following code to do so:

In [23]:
output_submission_csv('kaggle/svm_submission_fashion.csv', svm_fashion.predict(X_test_fashion))

weights [ 5.90152022e-25 -5.22173439e-25  2.82103032e-25  2.39361989e-24
  2.68355234e-23  8.88616122e-23  1.69776097e-22  2.41501196e-22
  2.52282463e-22 -1.53507341e-23 -6.56442018e-22 -7.84248323e-22
 -2.69435564e-23  2.27749746e-22  2.60363012e-22  4.92224072e-22
 -5.20067640e-22 -1.08609645e-21 -4.86645262e-22  3.55478642e-24
  1.54230488e-22  8.91688212e-23  1.43199135e-22  3.79013570e-23
  4.93230573e-24  1.88592102e-24 -1.34982150e-23 -1.97138288e-24
 -1.05701862e-24 -4.77654373e-24 -1.17510418e-23  3.56747689e-24
  9.34785994e-23  2.32395940e-22  4.32549502e-22  2.29771074e-22
 -1.99241852e-23 -6.30730047e-22 -1.03438919e-21 -6.77743522e-22
 -4.72566318e-22 -5.97882156e-22 -8.34554527e-22 -7.90058641e-22
 -6.37273112e-22 -1.03507698e-21 -7.54234918e-22 -6.46398646e-22
 -4.16723331e-22  1.06697878e-22  1.96110489e-22  9.60698785e-23
 -4.57088226e-24  4.38404609e-24 -9.62787158e-24 -1.56332333e-23
 -3.93929983e-24 -1.13293377e-23 -9.38096446e-24  2.09027796e-23
  2.18624041e-22 

## Train SVM on Rice

In [31]:
lr = 0.5
n_epochs = 10
reg_const = 0.05

svm_RICE = SVM(n_class_RICE, lr, n_epochs, reg_const)
svm_RICE.train(X_train_RICE, y_train_RICE)

[[6.48500000e+03 5.65300000e+03 1.49098010e+02 ... 3.30327000e+02
  6.51029553e-01 3.01491124e+00]
 [1.56090000e+04 7.47100000e+03 1.47544293e+02 ... 3.48779000e+02
  7.71770091e-01 2.25414994e+00]
 [1.39540000e+04 8.48200000e+03 1.55140680e+02 ... 3.73781000e+02
  7.62910670e-01 2.19843235e+00]
 ...
 [1.27250000e+04 9.06000000e+03 1.58431151e+02 ... 3.92347000e+02
  7.39600829e-01 2.15688949e+00]
 [7.93600000e+03 7.02200000e+03 1.67978647e+02 ... 3.74547000e+02
  6.29010715e-01 3.10674259e+00]
 [1.46640000e+04 9.06900000e+03 1.61453745e+02 ... 3.86285000e+02
  7.63754140e-01 2.22164340e+00]]


In [32]:
pred_svm = svm_RICE.predict(X_train_RICE)
print('The training accuracy is given by: %f' % (get_acc(pred_svm, y_train_RICE)))

weights [4.30034223e-04 6.27236836e-02 1.57484273e-03 9.35521792e-04
 1.43957656e-05 6.41732556e-02 1.19548224e-03 1.06438165e-05
 4.09886610e-03 1.50246134e-05 3.01251347e-05]
X test [[6.48500000e+03 5.65300000e+03 1.49098010e+02 ... 3.30327000e+02
  6.51029553e-01 3.01491124e+00]
 [1.56090000e+04 7.47100000e+03 1.47544293e+02 ... 3.48779000e+02
  7.71770091e-01 2.25414994e+00]
 [1.39540000e+04 8.48200000e+03 1.55140680e+02 ... 3.73781000e+02
  7.62910670e-01 2.19843235e+00]
 ...
 [1.27250000e+04 9.06000000e+03 1.58431151e+02 ... 3.92347000e+02
  7.39600829e-01 2.15688949e+00]
 [7.93600000e+03 7.02200000e+03 1.67978647e+02 ... 3.74547000e+02
  6.29010715e-01 3.10674259e+00]
 [1.46640000e+04 9.06900000e+03 1.61453745e+02 ... 3.86285000e+02
  7.63754140e-01 2.22164340e+00]]
bias 0.26953125
[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1

### Validate SVM on Rice

In [33]:
pred_svm = svm_RICE.predict(X_val_RICE)
print('The validation accuracy is given by: %f' % (get_acc(pred_svm, y_val_RICE)))

weights [4.30034223e-04 6.27236836e-02 1.57484273e-03 9.35521792e-04
 1.43957656e-05 6.41732556e-02 1.19548224e-03 1.06438165e-05
 4.09886610e-03 1.50246134e-05 3.01251347e-05]
X test [[1.69600000e+03 6.03400000e+03 1.45247754e+02 ... 3.29532000e+02
  6.98264530e-01 2.70282590e+00]
 [1.09290000e+04 5.68700000e+03 1.61656415e+02 ... 3.50242000e+02
  5.82581439e-01 3.53071373e+00]
 [1.64310000e+04 8.12100000e+03 1.54569191e+02 ... 3.64219000e+02
  7.69297249e-01 2.28911021e+00]
 ...
 [9.95000000e+03 6.20300000e+03 1.63310889e+02 ... 3.55584000e+02
  6.16491685e-01 3.30952915e+00]
 [1.55990000e+04 8.72000000e+03 1.59645509e+02 ... 3.80860000e+02
  7.55432427e-01 2.25391602e+00]
 [4.44500000e+03 5.55800000e+03 1.44236967e+02 ... 3.22515000e+02
  6.71473024e-01 2.89362721e+00]]
bias 0.26953125
[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1

## Test SVM on Rice

In [27]:
pred_svm = svm_RICE.predict(X_test_RICE)
print('The testing accuracy is given by: %f' % (get_acc(pred_svm, y_test_RICE)))

weights [3.37085142e-02 4.39583279e-02 1.57974823e-03 5.75302147e-04
 1.42895870e-05 4.72877838e-02 9.26687950e-04 1.08753498e-05
 3.61611253e-03 9.94486269e-06 4.21316350e-05]
X test [[1.06470000e+04 6.25700000e+03 1.66294393e+02 ... 3.59071000e+02
  6.09839227e-01 3.43324248e+00]
 [1.19470000e+04 7.39300000e+03 1.43253832e+02 ... 3.46736000e+02
  7.72738767e-01 2.12742401e+00]
 [1.36170000e+04 8.91100000e+03 1.58713368e+02 ... 3.79484000e+02
  7.77587675e-01 2.18798900e+00]
 ...
 [1.06000000e+03 7.18500000e+03 1.55907666e+02 ... 3.59660000e+02
  6.97995072e-01 2.62311387e+00]
 [8.80700000e+03 7.46200000e+03 1.39140815e+02 ... 3.34619000e+02
  8.37459695e-01 2.02705462e+00]
 [8.54900000e+03 5.86600000e+03 1.55081390e+02 ... 3.44326000e+02
  6.21744981e-01 3.15361193e+00]]
bias 0.26953125
[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1

# Softmax Classifier (with SGD)

Next, you will train a Softmax classifier. This classifier consists of a linear function of the input data followed by a softmax function which outputs a vector of dimension C (number of classes) for each data point. Each entry of the softmax output vector corresponds to a confidence in one of the C classes, and like a probability distribution, the entries of the output vector sum to 1. We use a cross-entropy loss on this sotmax output to train the model. 

Check the following link as an additional resource on softmax classification: http://cs231n.github.io/linear-classify/#softmax

Once again we will train the classifier with SGD. This means you need to compute the gradients of the softmax cross-entropy loss function according to the weights and update the weights using this gradient. Check the following link to help with implementing the gradient updates: https://deepnotes.io/softmax-crossentropy

The softmax classifier has 3 hyperparameters that you can experiment with:
- **Learning rate** - As above, this controls how much the model weights are updated with respect to their gradient.
- **Number of Epochs** - As described for perceptron.
- **Regularization constant** - Hyperparameter to determine the strength of regularization. In this case, we minimize the L2 norm of the model weights as regularization, so the regularization constant is a coefficient on the L2 norm in the combined cross-entropy and regularization objective.

You will implement a softmax classifier using SGD in the **models/softmax.py**

The following code: 
- Creates an instance of the Softmax classifier class 
- The train function of the Softmax class is trained on the training data
- We use the predict function to find the training accuracy as well as the testing accuracy

## Train Softmax on Fashion-MNIST

In [34]:
lr = 0.5
n_epochs = 10
reg_const = 0.5

softmax_fashion = Softmax(n_class_fashion, lr, n_epochs, reg_const)
softmax_fashion.train(X_train_fashion, y_train_fashion)

scores dot product of train and weights [[0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]]
probabilities [[0.1 0.1 0.1 ... 0.1 0.1 0.1]
 [0.1 0.1 0.1 ... 0.1 0.1 0.1]
 [0.1 0.1 0.1 ... 0.1 0.1 0.1]
 ...
 [0.1 0.1 0.1 ... 0.1 0.1 0.1]
 [0.1 0.1 0.1 ... 0.1 0.1 0.1]
 [0.1 0.1 0.1 ... 0.1 0.1 0.1]]
scores dot product of train and weights [[  11946.27245052  -17757.57376929  126301.83974869 ... -111737.51825605
     9573.41714565  -14022.02457064]
 [  37733.54634002   57103.92723146   38614.81208194 ... -127677.7003003
   -21645.3861536   -38874.26201239]
 [   3520.69827255   17734.76409415   47152.74581291 ...  -63834.85819496
   -19658.77808076    7991.11816155]
 ...
 [  13607.71365344   14810.99928293   78609.62279301 ... -121053.20397953
    -2593.77251971  -27075.83046029]
 [ -59222.86713458 -100691.65519173  -10172.10335672 ...  128987.06785917
    75538.80779587   40520.05401067]

c:\Users\azaan\OneDrive\Desktop\Deep Learning for Computer Vision HW\assignment1_cs444\models\softmax.py:58: RuntimeWarning: overflow encountered in exp
  probabilities = np.exp(z) / np.sum(np.exp(z), axis=1, keepdims=True) # aka softmax
c:\Users\azaan\OneDrive\Desktop\Deep Learning for Computer Vision HW\assignment1_cs444\models\softmax.py:58: RuntimeWarning: invalid value encountered in divide
  probabilities = np.exp(z) / np.sum(np.exp(z), axis=1, keepdims=True) # aka softmax


scores dot product of train and weights [[nan nan nan ... nan nan nan]
 [nan nan nan ... nan nan nan]
 [nan nan nan ... nan nan nan]
 ...
 [nan nan nan ... nan nan nan]
 [nan nan nan ... nan nan nan]
 [nan nan nan ... nan nan nan]]
probabilities [[nan nan nan ... nan nan nan]
 [nan nan nan ... nan nan nan]
 [nan nan nan ... nan nan nan]
 ...
 [nan nan nan ... nan nan nan]
 [nan nan nan ... nan nan nan]
 [nan nan nan ... nan nan nan]]
scores dot product of train and weights [[nan nan nan ... nan nan nan]
 [nan nan nan ... nan nan nan]
 [nan nan nan ... nan nan nan]
 ...
 [nan nan nan ... nan nan nan]
 [nan nan nan ... nan nan nan]
 [nan nan nan ... nan nan nan]]
probabilities [[nan nan nan ... nan nan nan]
 [nan nan nan ... nan nan nan]
 [nan nan nan ... nan nan nan]
 ...
 [nan nan nan ... nan nan nan]
 [nan nan nan ... nan nan nan]
 [nan nan nan ... nan nan nan]]
scores dot product of train and weights [[nan nan nan ... nan nan nan]
 [nan nan nan ... nan nan nan]
 [nan nan nan ... nan 

In [35]:
pred_softmax = softmax_fashion.predict(X_train_fashion)
print('The training accuracy is given by: %f' % (get_acc(pred_softmax, y_train_fashion)))

The training accuracy is given by: 9.954000


### Validate Softmax on Fashion-MNIST

In [36]:
pred_softmax = softmax_fashion.predict(X_val_fashion)
print('The validation accuracy is given by: %f' % (get_acc(pred_softmax, y_val_fashion)))

The validation accuracy is given by: 10.230000


### Testing Softmax on Fashion-MNIST

In [37]:
pred_softmax = softmax_fashion.predict(X_test_fashion)
print('The testing accuracy is given by: %f' % (get_acc(pred_softmax, y_test_fashion)))

The testing accuracy is given by: 10.000000


### Softmax_Fashion-MNIST Kaggle Submission

Once you are satisfied with your solution and test accuracy output a file to submit your test set predictions to the Kaggle for Assignment 1 Fashion-MNIST. Use the following code to do so:

In [38]:
# output_submission_csv('kaggle/softmax_submission_fashion.csv', softmax_fashion.predict(X_test_fashion))

## Train Softmax on Rice

In [39]:
lr = 0.5
n_epochs = 10
reg_const = 0.05

softmax_RICE = Softmax(n_class_RICE, lr, n_epochs, reg_const)
softmax_RICE.train(X_train_RICE, y_train_RICE)

scores dot product of train and weights [[0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0.]
 [0. 0

In [40]:
pred_softmax = softmax_RICE.predict(X_train_RICE)
print('The training accuracy is given by: %f' % (get_acc(pred_softmax, y_train_RICE)))

The training accuracy is given by: 45.220420


### Validate Softmax on Rice

In [41]:
pred_softmax = softmax_RICE.predict(X_val_RICE)
print('The validation accuracy is given by: %f' % (get_acc(pred_softmax, y_val_RICE)))

The validation accuracy is given by: 43.854825


### Testing Softmax on Rice

In [42]:
pred_softmax = softmax_RICE.predict(X_test_RICE)
print('The testing accuracy is given by: %f' % (get_acc(pred_softmax, y_test_RICE)))

The testing accuracy is given by: 45.944460


# Logistic Classifier

The Logistic Classifier has 2 hyperparameters that you can experiment with:
- **Learning rate** - similar to as defined above in Perceptron, this parameter scales by how much the weights are changed according to the calculated gradient update. 
- **Number of Epochs** - As described for perceptron.
- **Threshold** - The decision boundary of the classifier.


You will implement the Logistic Classifier in the **models/logistic.py**

The following code: 
- Creates an instance of the Logistic classifier class 
- The train function of the Logistic class is trained on the training data
- We use the predict function to find the training accuracy as well as the testing accuracy

### Training Logistic Classifer

In [24]:
import sys
np.set_printoptions(threshold=sys.maxsize)

learning_rate = 0.5
n_epochs = 10
threshold = 0.0

lr = Logistic(learning_rate, n_epochs, threshold)
lr.train(X_train_RICE, y_train_RICE)

w [-8.39259096e+02 -1.30553272e+02  3.15706133e+00 -8.71272747e-01
  2.78836322e-02 -1.32264389e+02  2.49021487e-01  6.94820619e-03
  4.46269606e+00  3.00069974e-03  1.52045298e-01]
w [5.90092430e+02 1.49751386e+03 4.42082663e+01 1.32141098e+01
 2.84583701e-01 1.54139018e+03 2.40272434e+01 1.68150219e-01
 9.67757562e+01 1.83134275e-01 9.53227369e-01]
w [-2.51777729e+03 -3.91659816e+02  9.47118399e+00 -2.61381824e+00
  8.36508967e-02 -3.96793167e+02  7.47064461e-01  2.08446186e-02
  1.33880882e+01  9.00209921e-03  4.56135895e-01]
w [-1.08842576e+03  1.23640732e+03  5.05223889e+01  1.14715643e+01
  3.40350965e-01  1.27686140e+03  2.45252863e+01  1.82046631e-01
  1.05701148e+02  1.89135675e-01  1.25731797e+00]
w [-3.94056186e+03 -5.54047131e+02  1.80383597e+01 -3.46854372e+00
  1.53835604e-01 -5.59999198e+02  2.64526039e+00  4.45057491e-02
  2.75265650e+01  2.62003402e-02  8.01014412e-01]
w [-2.51121034e+03  1.07402000e+03  5.90895646e+01  1.06168388e+01
  4.10535673e-01  1.11365537e+03  

c:\Users\azaan\OneDrive\Desktop\Deep Learning for Computer Vision HW\assignment1_cs444\models\logistic.py:29: RuntimeWarning: overflow encountered in exp
  return 1 / (1 + np.exp(-z))


In [25]:
pred_lr = lr.predict(X_train_RICE)
print('The training accuracy is given by: %f' % (get_acc(pred_lr, y_train_RICE)))

The training accuracy is given by: 66.336724


### Validate Logistic Classifer

In [27]:
pred_lr = lr.predict(X_val_RICE)
print('The validation accuracy is given by: %f' % (get_acc(pred_lr, y_val_RICE)))

The validation accuracy is given by: 67.418202


### Test Logistic Classifier

In [28]:
pred_lr = lr.predict(X_test_RICE)
print('The testing accuracy is given by: %f' % (get_acc(pred_lr, y_test_RICE)))

The testing accuracy is given by: 66.950784
